In [ ]:
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 14.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 16.0 MB/s eta 0:00:00


In [ ]:
!pip install accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.4/261.4 kB 4.3 MB/s eta 0:00:00


In [ ]:
!pip install sentencepiece

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 7.1 MB/s eta 0:00:00


In [ ]:
!pip install transformers[torch]


In [ ]:
from transformers import DebertaV2ForSequenceClassification, DebertaV2Tokenizer, Trainer, TrainingArguments,TFDistilBertForSequenceClassification,AutoTokenizer,AutoModelForSequenceClassification,DistilBertTokenizer
from datasets import load_dataset

In [ ]:
from transformers import DebertaV2ForSequenceClassification, DebertaV2Tokenizer, Trainer, TrainingArguments,TFDistilBertForSequenceClassification,AutoTokenizer,AutoModelForSequenceClassification,DistilBertTokenizer
from datasets import load_dataset

model_name = "distilbert-base-uncased"
tokenizer = DistilBertTokenizer.from_pretrained("distilbert-base-uncased")
model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)

dataset = load_dataset("glue", "mrpc")
# dataset_validation = dataset.shuffle(seed=42).select([i for i in range(50000)])
def tokenize_function(examples):
    return tokenizer(examples["sentence1"], examples["sentence2"], truncation=True, padding="max_length", max_length=128)
tokenized_datasets = dataset.map(tokenize_function, batched=True)

training_args = TrainingArguments(
    output_dir="./results/mrpc",
    evaluation_strategy="steps",
    eval_steps=50,
    learning_rate=1e-5,
    per_device_train_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.02,
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False,
)

tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/483 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

...

Generating validation split:   0%|          | 0/408 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1725 [00:00<?, ? examples/s]

Map:   0%|          | 0/3668 [00:00<?, ? examples/s]

Map:   0%|          | 0/408 [00:00<?, ? examples/s]

Map:   0%|          | 0/1725 [00:00<?, ? examples/s]

In [ ]:
import torch
validation_set = dataset['validation']
def evaluate_model(model, tokenizer, validation_set):
    model.eval()  # Set the model to evaluation mode

    correct_predictions = 0
    total_predictions = 0

    with torch.no_grad():
        for item in validation_set:
            inputs = tokenizer(item['sentence1'], item['sentence2'], return_tensors="pt", truncation=True, padding=True)
            outputs = model(**inputs)
            predictions = torch.argmax(outputs.logits, dim=1)
            correct_predictions += (predictions == item['label']).sum().item()
            total_predictions += 1

    accuracy = correct_predictions / total_predictions
    return accuracy

# Calculate accuracy
accuracy = evaluate_model(model, tokenizer, validation_set)
print(f"Accuracy: {accuracy}")

Accuracy: 0.6740196078431373


In [ ]:
tokenized_datasets

DatasetDict({
    train: Dataset({
        features: ['sentence1', 'sentence2', 'label', 'idx', 'input_ids', 'attention_mask'],
        num_rows: 3668
    })
    validation: Dataset({
        features: ['sentence1', 'sentence2', 'label', 'idx', 'input_ids', 'attention_mask'],
        num_rows: 408
    })
    test: Dataset({
        features: ['sentence1', 'sentence2', 'label', 'idx', 'input_ids', 'attention_mask'],
        num_rows: 1725
    })
})

In [ ]:
from transformers import Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets['train'],
    eval_dataset=tokenized_datasets["validation"],
    tokenizer=tokenizer
)

trainer.train()

TrainOutput(global_step=690, training_loss=0.47407998347627944, metrics={'train_runtime': 149.6703, 'train_samples_per_second': 73.522, 'train_steps_per_second': 4.61, 'total_flos': 364417813702656.0, 'train_loss': 0.47407998347627944, 'epoch': 3.0})

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
save_directory = "/content/drive/MyDrive/MyModelDirectory/MRPC"

In [ ]:
model.save_pretrained(save_directory)
tokenizer.save_pretrained(save_directory)

('/content/drive/MyDrive/MyModelDirectory/MRPC/tokenizer_config.json',
 '/content/drive/MyDrive/MyModelDirectory/MRPC/special_tokens_map.json',
 '/content/drive/MyDrive/MyModelDirectory/MRPC/vocab.txt',
 '/content/drive/MyDrive/MyModelDirectory/MRPC/added_tokens.json')

In [ ]:
from transformers import DistilBertTokenizer

model = AutoModelForSequenceClassification.from_pretrained(save_directory)
tokenizer = DistilBertTokenizer.from_pretrained(save_directory)

In [ ]:
dataset = load_dataset("glue", "mrpc")
validation_dataset = dataset["validation"]

def tokenize_function(examples):
    return tokenizer(examples["sentence1"], examples["sentence2"], truncation=True, padding="max_length", max_length=128)

tokenized_validation_dataset = validation_dataset.map(tokenize_function, batched=True)

Map:   0%|          | 0/408 [00:00<?, ? examples/s]

In [ ]:
from transformers import Trainer
import numpy as np

trainer = Trainer(model=model)

raw_pred, _, _ = trainer.predict(tokenized_validation_dataset)

# Apply softmax and then argmax to get the most likely class
predictions = np.argmax(raw_pred, axis=1)

In [ ]:
import numpy as np

# Apply softmax and then argmax to get the most likely class
predictions = np.argmax(raw_pred, axis=1)

In [ ]:
true_labels = validation_dataset["label"]

# Analyze the results
for i, (pred, label) in enumerate(zip(predictions, true_labels)):
    if pred != label:
        print(f"Index: {i}, Predicted: {pred}, Actual: {label}")
        print(f"Sentence 1: {validation_dataset[i]['sentence1']}")
        print(f"Sentence 2: {validation_dataset[i]['sentence2']}")
        print("-----")

Index: 6, Predicted: 1, Actual: 0
Sentence 1: While dioxin levels in the environment were up last year , they have dropped by 75 percent since the 1970s , said Caswell .
Sentence 2: The Institute said dioxin levels in the environment have fallen by as much as 76 percent since the 1970s .
-----
Index: 26, Predicted: 1, Actual: 0
Sentence 1: Cooley said he expects Muhammad will similarly be called as a witness at a pretrial hearing for Malvo .
Sentence 2: Lee Boyd Malvo will be called as a witness Wednesday in a pretrial hearing for fellow sniper suspect John Allen Muhammad .
-----
Index: 35, Predicted: 1, Actual: 0
Sentence 1: Bush wanted " to see an aircraft landing the same way that the pilots saw an aircraft landing , " White House press secretary Ari Fleischer said yesterday .
Sentence 2: On Tuesday , before Byrd 's speech , Fleischer said Bush wanted ' ' to see an aircraft landing the same way that the pilots saw an aircraft landing .
-----
Index: 42, Predicted: 1, Actual: 0
Senten

In [ ]:
accuracy = np.mean(predictions == true_labels)
print(f"Validation Accuracy: {accuracy}")

Validation Accuracy: 0.8063725490196079


# Finetuning

In [ ]:
def model_init():
    return AutoModelForSequenceClassification.from_pretrained(save_directory, num_labels=2)

In [ ]:
# dataset_train = tokenized_datasets['train'].shuffle(seed=42).select([i for i in range(50000)])
trainer = Trainer(
    model_init=model_init,
    args=training_args,
    train_dataset=tokenized_datasets['train'],
    eval_dataset=tokenized_datasets["validation"],
    tokenizer=tokenizer
)


In [ ]:
!pip install optuna

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 409.6/409.6 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 226.8/226.8 kB 21.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 7.4 MB/s eta 0:00:00


In [ ]:
best_run = trainer.hyperparameter_search(n_trials=10, direction="maximize")

[I 2023-11-29 03:12:18,875] A new study created in memory with name: no-name-28ab19f8-e49c-40ac-952e-176939ae65e3


[I 2023-11-29 03:13:06,781] Trial 0 finished with value: 0.37059342861175537 and parameters: {'learning_rate': 7.281495051129104e-05, 'num_train_epochs': 1, 'seed': 21, 'per_device_train_batch_size': 32}. Best is trial 0 with value: 0.37059342861175537.


[I 2023-11-29 03:13:49,756] Trial 1 finished with value: 0.40802547335624695 and parameters: {'learning_rate': 2.8597709136391473e-06, 'num_train_epochs': 1, 'seed': 9, 'per_device_train_batch_size': 32}. Best is trial 1 with value: 0.40802547335624695.


[I 2023-11-29 03:16:01,269] Trial 2 finished with value: 0.4704553186893463 and parameters: {'learning_rate': 1.1727001154899626e-05, 'num_train_epochs': 2, 'seed': 35, 'per_device_train_batch_size': 8}. Best is trial 2 with value: 0.4704553186893463.


[I 2023-11-29 03:18:46,155] Trial 3 finished with value: 0.4166034758090973 and parameters: {'learning_rate': 1.859479099998176e-06, 'num_train_epochs': 3, 'seed': 26, 'per_device_train_batch_size': 16}. Best is trial 2 with value: 0.4704553186893463.


...

[I 2023-11-29 03:24:02,871] Trial 5 pruned. 


[I 2023-11-29 03:24:19,812] Trial 6 pruned. 


[I 2023-11-29 03:24:40,409] Trial 7 pruned. 


[I 2023-11-29 03:25:00,711] Trial 8 pruned. 


[I 2023-11-29 03:26:43,943] Trial 9 pruned. 


In [ ]:
best_run

BestRun(run_id='4', objective=0.9636103510856628, hyperparameters={'learning_rate': 3.970266676634288e-05, 'num_train_epochs': 3, 'seed': 28, 'per_device_train_batch_size': 4}, run_summary=None)

In [ ]:
for n, v in best_run.hyperparameters.items():
    setattr(trainer.args, n, v)

trainer = Trainer(
    model_init=model_init,
    args=training_args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["validation"],
    tokenizer=tokenizer
)

trainer.train()

TrainOutput(global_step=2751, training_loss=0.31959256498391564, metrics={'train_runtime': 298.5576, 'train_samples_per_second': 36.857, 'train_steps_per_second': 9.214, 'total_flos': 364417813702656.0, 'train_loss': 0.31959256498391564, 'epoch': 3.0})

In [ ]:
model.save_pretrained(save_directory)
tokenizer.save_pretrained(save_directory)

('/content/drive/MyDrive/MyModelDirectory/MRPC/tokenizer_config.json',
 '/content/drive/MyDrive/MyModelDirectory/MRPC/special_tokens_map.json',
 '/content/drive/MyDrive/MyModelDirectory/MRPC/vocab.txt',
 '/content/drive/MyDrive/MyModelDirectory/MRPC/added_tokens.json')

In [ ]:
from transformers import Trainer
import numpy as np

# trainer = Trainer(model=model_init())

raw_pred, _, _ = trainer.predict(tokenized_validation_dataset)

# Apply softmax and then argmax to get the most likely class
predictions = np.argmax(raw_pred, axis=1)

In [ ]:
true_labels = validation_dataset["label"]

# Analyze the results
for i, (pred, label) in enumerate(zip(predictions, true_labels)):
    if pred != label:
        print(f"Index: {i}, Predicted: {pred}, Actual: {label}")
        print(f"Sentence 1: {validation_dataset[i]['sentence1']}")
        print(f"Sentence 2: {validation_dataset[i]['sentence2']}")
        print("-----")

Index: 6, Predicted: 1, Actual: 0
Sentence 1: While dioxin levels in the environment were up last year , they have dropped by 75 percent since the 1970s , said Caswell .
Sentence 2: The Institute said dioxin levels in the environment have fallen by as much as 76 percent since the 1970s .
-----
Index: 15, Predicted: 0, Actual: 1
Sentence 1: Unable to find a home for him , a judge told mental health authorities they needed to find supervised housing and treatment for DeVries somewhere in California .
Sentence 2: The judge had told the state Department of Mental Health to find supervised housing and treatment for DeVries somewhere in California .
-----
Index: 22, Predicted: 1, Actual: 0
Sentence 1: The driver , Eugene Rogers , helped to remove children from the bus , Wood said .
Sentence 2: At the accident scene , the driver was " covered in blood " but helped to remove children , Wood said .
-----
Index: 25, Predicted: 0, Actual: 1
Sentence 1: Its closest living relatives are a family fr

In [ ]:
accuracy = np.mean(predictions == true_labels)
print(f"Validation Accuracy: {accuracy}")

Validation Accuracy: 0.8161764705882353


In [ ]:
!pip install textattack

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 436.8/436.8 kB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 9.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 387.2/387.2 kB 41.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 769.7/769.7 kB 67.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.3/143.3 kB 23.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 86.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.4/41.4 MB 26.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.5/97.5 kB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.3/139.3 kB 21.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.4/53.4 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.7/19.7 MB 52.

In [ ]:
save_directory = '/content/drive/MyDrive/MRPC'
model = AutoModelForSequenceClassification.from_pretrained(save_directory)
tokenizer = DistilBertTokenizer.from_pretrained(save_directory)

# TextFooler

In [ ]:
from textattack.models.wrappers import HuggingFaceModelWrapper
from textattack.datasets import HuggingFaceDataset
from textattack.attack_recipes import TextFoolerJin2019
from textattack import Attacker, AttackArgs
from textattack.loggers import CSVLogger

In [ ]:
model_wrapper = HuggingFaceModelWrapper(model, tokenizer)
dataset = HuggingFaceDataset("glue", "mrpc", split="train")
attack = TextFoolerJin2019.build(model_wrapper)
attack_args = AttackArgs(
    num_examples=1000,
    log_to_csv="log_1_train.csv",
    checkpoint_interval=5,
    checkpoint_dir="checkpoints",
    disable_stdout=False
)

textattack: Loading datasets dataset glue, subset mrpc, split train.
textattack: Unknown if model of class <class 'transformers.models.distilbert.modeling_distilbert.DistilBertForSequenceClassification'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


In [ ]:
attacker = Attacker(attack, dataset, attack_args)
attacker.attack_dataset()

textattack: Logging to CSV at path log_1_train.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       



[Succeeded / Failed / Skipped / Total] 13 / 3 / 2 / 18:   9%|▉         | 18/200 [32:27<5:28:13, 108.21s/it]
textattack: CSVLogger exiting without calling flush().


  0%|          | 1/1000 [00:14<4:01:00, 14.47s/it]

[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:14<4:01:22, 14.50s/it]

[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:14<2:00:49,  7.26s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[Equivalent (92%)]] --> [[Not_equivalent (50%)]]

[[[[Sentence1]]]]: Amrozi [[accused]] his brother , whom he called " the [[witness]] " , of deliberately [[distorting]] his evidence .
[[[[Sentence2]]]]: Referring to him as only " the witness " , Amrozi accused his brother of [[deliberately]] [[distorting]] his evidence .

[[[[Sentence1]]]]: Amrozi [[arraigned]] his brother , whom he called " the [[eyewitness]] " , of deliberately [[warped]] his evidence .
[[[[Sentence2]]]]: Referring to him as only " the witness " , Amrozi accused his brother of [[wantonly]] [[malformed]] his evidence .


--------------------------------------------- Result 2 ---------------------------------------------
[[Equivalent (70%)]] --> [[[SKIPPED]]]

[[[[Sentence1]]]]: Yucaipa owned Dominick 's before selling the chain to Safeway in 1998 for $ 2.5 billion .
[[[[Sentence2]]]]: Yucaipa bought Dominick 's in 19



[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 3/1000 [00:17<1:38:56,  5.95s/it]

[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:17<1:39:10,  5.97s/it]

...

--------------------------------------------- Result 999 ---------------------------------------------
[[Equivalent (80%)]] --> [[Not_equivalent (52%)]]

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson testified at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , according to his written [[testimony]] .

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson testified at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , according to his written [[martyrdom]] .






[Succeeded / Failed / Skipped / Total] 744 / 53 / 203 / 1000: 100%|██████████| 1000/1000 [47:40<00:00,  2.86s/it]textattack: Saving checkpoint under "checkpoints/1701305282028.ta.chkpt" at 2023-11-30 00:48:02 after 1000 attacks.


--------------------------------------------- Result 1000 ---------------------------------------------
[[Not_equivalent (80%)]] --> [[[FAILED]]]

[[[[Sentence1]]]]: The Standard & Poor 's 500 Index slipped 3.14 points , or 0.29 percent , to 1,071.99 .
[[[[Sentence2]]]]: The Standard & Poor 's retail index < .RLX > was up more than 1.5 percent .







[Succeeded / Failed / Skipped / Total] 744 / 53 / 203 / 1000: 100%|██████████| 1000/1000 [47:40<00:00,  2.86s/it]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 744    |
| Number of failed attacks:     | 53     |
| Number of skipped attacks:    | 203    |
| Original accuracy:            | 79.7%  |
| Accuracy under attack:        | 5.3%   |
| Attack success rate:          | 93.35% |
| Average perturbed word %:     | 12.21% |
| Average num. words per input: | 38.84  |
| Avg num queries:              | 172.33 |
+-------------------------------+--------+


# DeepWordBug


In [ ]:
from textattack.attack_recipes import DeepWordBugGao2018

In [ ]:
model_wrapper = HuggingFaceModelWrapper(model, tokenizer)
dataset = HuggingFaceDataset("glue", "mrpc", split="train")
attack = DeepWordBugGao2018.build(model_wrapper)
attack_args = AttackArgs(
    num_examples=1000,
    log_to_csv="log_deepword_train.csv",
    checkpoint_interval=5,
    checkpoint_dir="checkpoints",
    disable_stdout=False
)

textattack: Loading datasets dataset glue, subset mrpc, split train.
textattack: Unknown if model of class <class 'transformers.models.distilbert.modeling_distilbert.DistilBertForSequenceClassification'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


In [ ]:
attacker = Attacker(attack, dataset, attack_args)
attacker.attack_dataset()

textattack: Logging to CSV at path log_deepword_train.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  unk
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterSubstitution(
        (random_one):  True
      )
    (2): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (3): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    )
  (constraints): 
    (0): LevenshteinEditDistance(
        (max_edit_distance):  30
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 



[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:00<06:32,  2.54it/s]

--------------------------------------------- Result 1 ---------------------------------------------
[[Equivalent (92%)]] --> [[Not_equivalent (50%)]]

[[[[Sentence1]]]]: [[Amrozi]] [[accused]] his brother , whom he called " the witness " , of deliberately distorting his evidence .
[[[[Sentence2]]]]: [[Referring]] to him as only " the witness " , [[Amrozi]] accused his brother of [[deliberately]] distorting his evidence .

[[[[Sentence1]]]]: [[AAmrozi]] [[accsued]] his brother , whom he called " the witness " , of deliberately distorting his evidence .
[[[[Sentence2]]]]: [[gReferring]] to him as only " the witness " , [[Amrzi]] accused his brother of [[delberately]] distorting his evidence .


--------------------------------------------- Result 2 ---------------------------------------------
[[Equivalent (70%)]] --> [[[SKIPPED]]]

[[[[Sentence1]]]]: Yucaipa owned Dominick 's before selling the chain to Safeway in 1998 for $ 2.5 billion .
[[[[Sentence2]]]]: Yucaipa bought Dominick 's i

[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:01<08:41,  1.91it/s]

...

--------------------------------------------- Result 999 ---------------------------------------------
[[Equivalent (80%)]] --> [[Not_equivalent (55%)]]

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson [[testified]] at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , [[according]] to his written [[testimony]] .

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson [[tiestified]] at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , [[Raccording]] to his written [[testiXony]] .




[Succeeded / Failed / Skipped / Total] 678 / 119 / 203 / 1000: 100%|██████████| 1000/1000 [15:28<00:00,  1.08it/s]textattack: Saving checkpoint under "checkpoints/1701306779236.ta.chkpt" at 2023-11-30 01:12:59 after 1000 attacks.


--------------------------------------------- Result 1000 ---------------------------------------------
[[Not_equivalent (80%)]] --> [[[FAILED]]]

[[[[Sentence1]]]]: The Standard & Poor 's 500 Index slipped 3.14 points , or 0.29 percent , to 1,071.99 .
[[[[Sentence2]]]]: The Standard & Poor 's retail index < .RLX > was up more than 1.5 percent .







[Succeeded / Failed / Skipped / Total] 678 / 119 / 203 / 1000: 100%|██████████| 1000/1000 [15:28<00:00,  1.08it/s]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 678    |
| Number of failed attacks:     | 119    |
| Number of skipped attacks:    | 203    |
| Original accuracy:            | 79.7%  |
| Accuracy under attack:        | 11.9%  |
| Attack success rate:          | 85.07% |
| Average perturbed word %:     | 11.65% |
| Average num. words per input: | 38.84  |
| Avg num queries:              | 58.91  |
+-------------------------------+--------+


In [ ]:
from textattack.models.wrappers import HuggingFaceModelWrapper
from textattack.datasets import HuggingFaceDataset
from textattack.attack_recipes import TextBuggerLi2018
from textattack import Attacker, AttackArgs
from textattack.loggers import CSVLogger

# TextBugger

In [ ]:
model_wrapper = HuggingFaceModelWrapper(model, tokenizer)
dataset = HuggingFaceDataset("glue", "mrpc", split="train")
attack = TextBuggerLi2018.build(model_wrapper)
attack_args = AttackArgs(
    num_examples=1000,
    log_to_csv="log_textbugger_train.csv",
    checkpoint_interval=5,
    checkpoint_dir="checkpoints",
    disable_stdout=False
)

textattack: Loading datasets dataset glue, subset mrpc, split train.
textattack: Unknown if model of class <class 'transformers.models.distilbert.modeling_distilbert.DistilBertForSequenceClassification'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


In [ ]:
attacker = Attacker(attack, dataset, attack_args)
attacker.attack_dataset()

textattack: Logging to CSV at path log_textbugger_train.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (2): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (3): WordSwapHomoglyphSwap
    (4): WordSwapEmbedding(
        (max_candidates):  5
        (embedding):  WordEmbedding
      )
    )
  (constraints): 
    (0): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8
        (window_size):  inf
        (skip_text_shorter_than_window):  False
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 



[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:10<1:31:06,  5.48s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[Equivalent (92%)]] --> [[Not_equivalent (50%)]]

[[[[Sentence1]]]]: [[Amrozi]] accused his brother , whom he called " the witness " , of [[deliberately]] distorting his evidence .
[[[[Sentence2]]]]: Referring to him as only " the [[witness]] " , Amrozi accused his brother of deliberately [[distorting]] his evidence .

[[[[Sentence1]]]]: [[Amr]] [[ozi]] accused his brother , whom he called " the witness " , of [[d]] [[eliberately]] distorting his evidence .
[[[[Sentence2]]]]: Referring to him as only " the [[wіtness]] " , Amrozi accused his brother of deliberately [[warp]] his evidence .


--------------------------------------------- Result 2 ---------------------------------------------
[[Equivalent (70%)]] --> [[[SKIPPED]]]

[[[[Sentence1]]]]: Yucaipa owned Dominick 's before selling the chain to Safeway in 1998 for $ 2.5 billion .
[[[[Sentence2]]]]: Yucaipa bought Dominick 's in 19

[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:13<1:12:36,  4.37s/it]

...

--------------------------------------------- Result 999 ---------------------------------------------
[[Equivalent (80%)]] --> [[Not_equivalent (52%)]]

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson [[testified]] at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , according to his written [[testimony]] .

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson [[testi]] [[fied]] at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , according to his written [[tеstimony]] .




[Succeeded / Failed / Skipped / Total] 749 / 48 / 203 / 1000: 100%|██████████| 1000/1000 [24:36<00:00,  1.48s/it]textattack: Saving checkpoint under "checkpoints/1701309276035.ta.chkpt" at 2023-11-30 01:54:36 after 1000 attacks.


--------------------------------------------- Result 1000 ---------------------------------------------
[[Not_equivalent (80%)]] --> [[[FAILED]]]

[[[[Sentence1]]]]: The Standard & Poor 's 500 Index slipped 3.14 points , or 0.29 percent , to 1,071.99 .
[[[[Sentence2]]]]: The Standard & Poor 's retail index < .RLX > was up more than 1.5 percent .







[Succeeded / Failed / Skipped / Total] 749 / 48 / 203 / 1000: 100%|██████████| 1000/1000 [24:36<00:00,  1.48s/it]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 749    |
| Number of failed attacks:     | 48     |
| Number of skipped attacks:    | 203    |
| Original accuracy:            | 79.7%  |
| Accuracy under attack:        | 4.8%   |
| Attack success rate:          | 93.98% |
| Average perturbed word %:     | 26.52% |
| Average num. words per input: | 38.84  |
| Avg num queries:              | 91.88  |
+-------------------------------+--------+


# PWWS


In [ ]:
from textattack.models.wrappers import HuggingFaceModelWrapper
from textattack.datasets import HuggingFaceDataset
from textattack.attack_recipes import PWWSRen2019
from textattack import Attacker, AttackArgs
from textattack.loggers import CSVLogger

textattack: Updating TextAttack package dependencies.
textattack: Downloading NLTK required packages.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package omw to /root/nltk_data...
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Unzipping taggers/universal_tagset.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [ ]:
model_wrapper = HuggingFaceModelWrapper(model, tokenizer)
dataset = HuggingFaceDataset("glue", "mrpc", split="validation")
attack = PWWSRen2019.build(model_wrapper)
attack_args = AttackArgs(
    num_examples=200,
    log_to_csv="log_PWWS_train.csv",
    checkpoint_interval=5,
    checkpoint_dir="checkpoints",
    disable_stdout=False
)

In [ ]:
attacker = Attacker(attack, dataset, attack_args)
attacker.attack_dataset()

textattack: Logging to CSV at path log_PWWS_train.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  weighted-saliency
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapWordNet
  (constraints): 
    (0): RepeatModification
    (1): StopwordModification
  (is_black_box):  True
) 



[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:04<35:18,  2.12s/it]  

--------------------------------------------- Result 1 ---------------------------------------------
[[Equivalent (92%)]] --> [[Not_equivalent (54%)]]

[[[[Sentence1]]]]: Amrozi [[accused]] his brother , whom he called " the [[witness]] " , of deliberately [[distorting]] his evidence .
[[[[Sentence2]]]]: [[Referring]] to him as only " the [[witness]] " , Amrozi accused his brother of deliberately [[distorting]] his [[evidence]] .

[[[[Sentence1]]]]: Amrozi [[impeach]] his brother , whom he called " the [[viewer]] " , of deliberately [[garble]] his evidence .
[[[[Sentence2]]]]: [[touch]] to him as only " the [[looker]] " , Amrozi accused his brother of deliberately [[falsify]] his [[show]] .


--------------------------------------------- Result 2 ---------------------------------------------
[[Equivalent (70%)]] --> [[[SKIPPED]]]

[[[[Sentence1]]]]: Yucaipa owned Dominick 's before selling the chain to Safeway in 1998 for $ 2.5 billion .
[[[[Sentence2]]]]: Yucaipa bought Dominick 's in

[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:07<40:04,  2.41s/it]

...

--------------------------------------------- Result 999 ---------------------------------------------
[[Equivalent (80%)]] --> [[Not_equivalent (52%)]]

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson testified at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , [[according]] to his written [[testimony]] .

[[[[Sentence1]]]]: " We must not engage in borough warfare , " Thompson testified at a budget hearing by the City Council 's Finance Committee .
[[[[Sentence2]]]]: " We must not engage in borough warfare , " the Comptroller William Thompson told the Council , [[harmonise]] to his written [[testimonial]] .




[Succeeded / Failed / Skipped / Total] 716 / 81 / 203 / 1000: 100%|██████████| 1000/1000 [1:06:27<00:00,  3.99s/it]textattack: Saving checkpoint under "checkpoints/1701314158887.ta.chkpt" at 2023-11-30 03:15:58 after 1000 attacks.


--------------------------------------------- Result 1000 ---------------------------------------------
[[Not_equivalent (80%)]] --> [[[FAILED]]]

[[[[Sentence1]]]]: The Standard & Poor 's 500 Index slipped 3.14 points , or 0.29 percent , to 1,071.99 .
[[[[Sentence2]]]]: The Standard & Poor 's retail index < .RLX > was up more than 1.5 percent .







[Succeeded / Failed / Skipped / Total] 716 / 81 / 203 / 1000: 100%|██████████| 1000/1000 [1:06:27<00:00,  3.99s/it]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 716    |
| Number of failed attacks:     | 81     |
| Number of skipped attacks:    | 203    |
| Original accuracy:            | 79.7%  |
| Accuracy under attack:        | 8.1%   |
| Attack success rate:          | 89.84% |
| Average perturbed word %:     | 11.57% |
| Average num. words per input: | 38.84  |
| Avg num queries:              | 276.69 |
+-------------------------------+--------+

# IGA

In [ ]:


from textattack.models.wrappers import HuggingFaceModelWrapper
from textattack.datasets import HuggingFaceDataset
from textattack.attack_recipes import IGAWang2019
from textattack import Attacker, AttackArgs
from textattack.loggers import CSVLogger

In [ ]:
model_wrapper = HuggingFaceModelWrapper(model, tokenizer)
dataset = HuggingFaceDataset("glue", "mrpc", split="validation")
attack = IGAWang2019.build(model_wrapper)
attack_args = AttackArgs(
    num_examples=200,
    log_to_csv="log_IGA_val.csv",
    checkpoint_interval=5,
    checkpoint_dir="checkpoints",
    disable_stdout=False
)

textattack: Loading datasets dataset glue, subset mrpc, split validation.
textattack: Downloading https://textattack.s3.amazonaws.com/word_embeddings/paragramcf.
100%|██████████| 481M/481M [00:14<00:00, 34.0MB/s]
textattack: Unzipping file /root/.cache/textattack/tmpcj9xy5vm.zip to /root/.cache/textattack/word_embeddings/paragramcf.
textattack: Successfully saved word_embeddings/paragramcf to cache.
textattack: Unknown if model of class <class 'transformers.models.distilbert.modeling_distilbert.DistilBertForSequenceClassification'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


In [ ]:
attacker = Attacker(attack, dataset, attack_args)
attacker.attack_dataset()

textattack: Logging to CSV at path log_IGA_val.csv


Attack(
  (search_method): ImprovedGeneticAlgorithm(
    (pop_size):  60
    (max_iters):  20
    (temp):  0.3
    (give_up_if_no_improvement):  False
    (post_crossover_check):  False
    (max_crossover_retries):  20
    (max_replace_times_per_index):  5
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): MaxWordsPerturbed(
        (max_percent):  0.2
        (compare_against_original):  True
      )
    (1): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (max_mse_dist):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  False
      )
    (2): StopwordModification
  (is_black_box):  True
) 



[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/200 [00:24<1:22:16, 24.81s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[Equivalent (97%)]] --> [[Not_equivalent (62%)]]

[[[[Sentence1]]]]: He said the foodservice [[pie]] business doesn 't [[fit]] the company 's long-term growth [[strategy]] .
[[[[Sentence2]]]]: " [[The]] foodservice pie [[business]] does not fit our long-term growth strategy .

[[[[Sentence1]]]]: He said the foodservice [[cobbler]] business doesn 't [[readjusted]] the company 's long-term growth [[strategic]] .
[[[[Sentence2]]]]: " [[To]] foodservice pie [[enterprising]] does not fit our long-term growth strategy .




[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|          | 2/200 [05:36<9:15:11, 168.24s/it]

...

--------------------------------------------- Result 199 ---------------------------------------------
[[Equivalent (89%)]] --> [[Not_equivalent (58%)]]

[[[[Sentence1]]]]: Cindy Yeast , a 50-year-old Washington-area publicist , says she began taking supplements two years ago in part to avoid [[mild]] [[dementia]] that affects her elderly parents .
[[[[Sentence2]]]]: She started [[taking]] supplements two years ago - partly to stave off mild dementia that affects her elderly parents .

[[[[Sentence1]]]]: Cindy Yeast , a 50-year-old Washington-area publicist , says she began taking supplements two years ago in part to avoid [[soft]] [[lunacy]] that affects her elderly parents .
[[[[Sentence2]]]]: She started [[adopt]] supplements two years ago - partly to stave off mild dementia that affects her elderly parents .




[Succeeded / Failed / Skipped / Total] 147 / 16 / 37 / 200: 100%|██████████| 200/200 [2:39:34<00:00, 47.87s/it]textattack: Saving checkpoint under "checkpoints/1701401009425.ta.chkpt" at 2023-12-01 03:23:29 after 200 attacks.


--------------------------------------------- Result 200 ---------------------------------------------
[[Equivalent (93%)]] --> [[Not_equivalent (60%)]]

[[[[Sentence1]]]]: The two are not related , but have referred to each other as father and son .
[[[[Sentence2]]]]: He 's not [[related]] to Malvo , but the two have referred to each other as father and son .

[[[[Sentence1]]]]: The two are not related , but have referred to each other as father and son .
[[[[Sentence2]]]]: He 's not [[thereto]] to Malvo , but the two have referred to each other as father and son .







[Succeeded / Failed / Skipped / Total] 147 / 16 / 37 / 200: 100%|██████████| 200/200 [2:39:34<00:00, 47.87s/it]


+-------------------------------+---------+
| Attack Results                |         |
+-------------------------------+---------+
| Number of successful attacks: | 147     |
| Number of failed attacks:     | 16      |
| Number of skipped attacks:    | 37      |
| Original accuracy:            | 81.5%   |
| Accuracy under attack:        | 8.0%    |
| Attack success rate:          | 90.18%  |
| Average perturbed word %:     | 10.37%  |
| Average num. words per input: | 39.34   |
| Avg num queries:              | 3507.04 |
+-------------------------------+---------+
